<a href="https://colab.research.google.com/github/peteralexandercharles/AndroRAT/blob/master/Example_synthesize_TTS_Mozilla_with_TTS_Portuguese_Corpus_using_universal_WaveRnn_finetunnig_TTS_Portuguese_Corpus.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**Cloning WaveRNN and TTS 
repository**

In [ ]:
import os
# clone Neural Vocoder WaveRNN
!git clone https://github.com/erogol/WaveRNN.git
os.chdir('WaveRNN')
!git checkout 12c8744
!pip install -r requirements.txt

# Download WaveRNN checkpoints
!rm saver-wavernn.zip
!wget https://www.dropbox.com/s/4a60kt3detcw3r6/checkpoint-wavernn-finetunnig-tts-portuguese-corpus-560900.zip?dl=0 -O saver-wavernn.zip
!unzip saver-wavernn.zip 

os.chdir('..')

# Clone TTS repository
!git clone https://github.com/Edresson/TTS -b TTS-Portuguese


Cloning into 'WaveRNN'...
remote: Enumerating objects: 636, done.
remote: Total 636 (delta 0), reused 0 (delta 0), pack-reused 636
Receiving objects: 100% (636/636), 39.09 MiB | 12.92 MiB/s, done.
Resolving deltas: 100% (365/365), done.
Note: checking out '12c8744'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by performing another checkout.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -b with the checkout command again. Example:

  git checkout -b <new-branch-name>

HEAD is now at 12c8744 raise an error when the mel spectragram is too short for the resnet
rm: cannot remove 'saver-wavernn.zip': No such file or directory
--2020-10-13 10:32:46--  https://www.dropbox.com/s/4a60kt3detcw3r6/checkpoint-wavernn-finetunnig-tts-portuguese-corpus-560900.zip?dl=0
Resolving www.dropbox.com (www.dropbox

In [ ]:
# Install TTS repository

# !python -m pip install -r TTS/requirements.txt
! python -m pip install  numpy==1.14.3 lws torch>=0.4.1 librosa==0.5.1 Unidecode==0.4.20 tensorboard tensorboardX Pillow flask scipy==0.19.0 lws tqdm phonemizer
#matplotlib==2.0.2
! apt-get install espeak



ERROR: yellowbrick 0.9.1 has requirement scipy>=1.0.0, but you'll have scipy 0.19.0 which is incompatible.
ERROR: xarray 0.15.1 has requirement numpy>=1.15, but you'll have numpy 1.14.3 which is incompatible.
ERROR: umap-learn 0.4.6 has requirement numpy>=1.17, but you'll have numpy 1.14.3 which is incompatible.
ERROR: umap-learn 0.4.6 has requirement scipy>=1.3.1, but you'll have scipy 0.19.0 which is incompatible.
ERROR: tifffile 2020.9.3 has requirement numpy>=1.15.1, but you'll have numpy 1.14.3 which is incompatible.
ERROR: tensorflow 2.3.0 has requirement numpy<1.19.0,>=1.16.0, but you'll have numpy 1.14.3 which is incompatible.
ERROR: tensorflow 2.3.0 has requirement scipy==1.4.1, but you'll have scipy 0.19.0 which is incompatible.
ERROR: spacy 2.2.4 has requirement numpy>=1.15.0, but you'll have numpy 1.14.3 which is incompatible.
ERROR: seaborn 0.11.0 has requirement numpy>=1.15, but you'll have numpy 1.14.3 which is incompatible.
ERROR: seaborn 0.11.0 has requirement scipy>=1

**Import modules**

In [ ]:
%load_ext autoreload
%autoreload 2
import os
import sys
import io
import torch 
import time
import numpy as np
from collections import OrderedDict

TTS_PATH = "../content/TTS"
WAVERNN_PATH ="../content/WaveRNN"
# add libraries into environment
sys.path.append(TTS_PATH) # set this if TTS is not installed globally
sys.path.append(WAVERNN_PATH) # set this if TTS is not installed globally

import pylab as plt
%pylab inline

from matplotlib import rcParams 
rcParams["figure.figsize"] = (16,5)
sys.path.append('')

import librosa
import librosa.display

from TTS.models.tacotron import Tacotron 
from TTS.layers import *
from TTS.utils.data import *
from TTS.utils.audio import AudioProcessor
from TTS.utils.generic_utils import load_config
from TTS.utils.text import text_to_sequence, phoneme_to_sequence
from TTS.utils.text.symbols import symbols, phonemes

import IPython
from IPython.display import Audio
from TTS.utils import *


from TTS.utils.visual import visualize
from matplotlib import pylab as plt

Populating the interactive namespace from numpy and matplotlib


/usr/local/lib/python3.6/dist-packages/IPython/core/magics/pylab.py:161: UserWarning: pylab import has clobbered these variables: ['plt']
`%matplotlib` prevents importing * from pylab and numpy
  "\n`%matplotlib` prevents importing * from pylab and numpy"




**Download Weights**




In [ ]:
# TTS Weights
!wget -c -q --show-progress -O ./TTS-TL-saver.zip https://www.dropbox.com/s/91etfwt4tvzjqyz/TTS-checkpoint-phonemizer-wavernn-381000.zip?dl=0
!ls
!rm config.json
!unzip TTS-TL-saver.zip
! mv checkpoint_381000.pth.tar checkpoint.pth.tar

./TTS-TL-saver.zip  100%[===================>]  73.59M  17.1MB/s    in 4.3s    
'=0.4.1'   sample_data	 TTS   TTS-TL-saver.zip   WaveRNN
rm: cannot remove 'config.json': No such file or directory
Archive:  TTS-TL-saver.zip
  inflating: checkpoint_381000.pth.tar  
  inflating: config.json             


In [ ]:
# Utils definitions
from TTS.utils.synthesis import visualize 
 
def plot_alignment_with_text(alignment,text, info=None):
    fig, ax = plt.subplots(figsize=(16, 10))
    im = ax.imshow(
        alignment.T, aspect='auto', origin='lower', interpolation=None)
    fig.colorbar(im, ax=ax)
    xlabel = 'Decoder timestep'
    if info is not None:
        xlabel += '\n\n' + info
    plt.xlabel(xlabel)
    plt.ylabel('Encoder timestep')
    plt.yticks(range(len(text)), list(text))
    plt.tight_layout()
    return fig


def synthesis(m, s, CONFIG, use_cuda, ap,language=None,WaveRNN=False):
    """ Given the text, synthesising the audio """
    if language is None:
      language=CONFIG.phoneme_language
    text_cleaner = [CONFIG.text_cleaner]
    # print(phoneme_to_sequence(s, text_cleaner))s
    # print(sequence_to_phoneme(phoneme_to_sequence(s, text_cleaner)))
    if CONFIG.use_phonemes:
        seq = np.asarray(
            phoneme_to_sequence(s, text_cleaner, language),
            dtype=np.int32)
    else:
        seq = np.asarray(text_to_sequence(s, text_cleaner), dtype=np.int32)
    chars_var = torch.from_numpy(seq).unsqueeze(0)
    if use_cuda:
        chars_var = chars_var.cuda()
    mel_spec, linear_spec, alignments, stop_tokens = m.forward(
        chars_var.long())
    linear_spec = linear_spec[0].data.cpu().numpy()
    mel_spec = mel_spec[0].data.cpu().numpy()
    alignment = alignments[0].cpu().data.numpy()
    if not WaveRNN:
      wav = ap.inv_spectrogram(linear_spec.T)
      wav = wav[:ap.find_endpoint(wav)]
    else:
      wav = wavernn.generate(torch.FloatTensor(mel_spec.T).unsqueeze(0).cuda(), batched=True, target=11000, overlap=550)
    return wav, alignment, linear_spec, mel_spec, stop_tokens

def tts(model, text, CONFIG, use_cuda, ap, figures=True,name='figure',language=None):
    t_1 = time.time()
    waveform, alignment, spectrogram,mel_spec, stop_tokens = synthesis(model, text, CONFIG, use_cuda, ap,language=language,WaveRNN=False) 
    print(" >  Run-time with Griffin lim: {}".format(time.time() - t_1))
    t_1 = time.time()
    waveform2, _, _,_,_= synthesis(model, text, CONFIG, use_cuda, ap,language=language,WaveRNN=True) 
    print("\n >  Run-time with WaveRNN: {}".format(time.time() - t_1))
    if figures:
        fig = plot_alignment_with_text(alignment,text)
        visualize(alignment, spectrogram, stop_tokens,text,250, CONFIG,mel_spec) 
        fig.savefig(os.path.join(OUT_FOLDER,'alig_'+name+'.png'))
    print("Vocoder WaveRNN:")    
    IPython.display.display(Audio(waveform2, rate=ap2.sample_rate))
    print("Vocoder Griffin-Lim :") 
    IPython.display.display(Audio(waveform, rate=ap.sample_rate))  
    
    return alignment, spectrogram, stop_tokens,waveform,waveform2
  


**Restore  TTS Model**

In [ ]:
# Set constants

MODEL_PATH = 'checkpoint.pth.tar'
CONFIG_PATH =  'TTS/config.json'
OUT_FOLDER = 'samples/'
try:
  os.mkdir(OUT_FOLDER)
except:
  pass

CONFIG = load_config(CONFIG_PATH)
use_cuda = True


VOCODER_MODEL_PATH = "WaveRNN/saver.pth.tar"
VOCODER_CONFIG_PATH = "WaveRNN/config_16K.json"
VOCODER_CONFIG = load_config(VOCODER_CONFIG_PATH)
use_cuda = True

In [ ]:
# load the model
ap2 = AudioProcessor(**VOCODER_CONFIG.audio)
ap = AudioProcessor(**CONFIG.audio)

num_chars = len(phonemes) if CONFIG.use_phonemes else len(symbols)
! mv checkpoint_381200.pth.tar checkpoint.pth.tar
model= Tacotron(num_chars, CONFIG.embedding_size, ap.num_freq, ap.num_mels, CONFIG.r, CONFIG.memory_size)

# load model state
if use_cuda:
    cp = torch.load(MODEL_PATH)
else:
    cp = torch.load(MODEL_PATH, map_location=lambda storage, loc: storage)

# load the model
model.load_state_dict(cp['model'])
if use_cuda:
    model.cuda()
model.eval()


 > Setting up Audio Processor...
 | > fft size: 2048, hop length: 200, win length: 800
 | > Audio Processor attributes.
   | > bits:None
   | > sample_rate:16000
   | > num_mels:80
   | > min_level_db:-100
   | > frame_shift_ms:12.5
   | > frame_length_ms:50
   | > ref_level_db:20
   | > num_freq:1025
   | > power:1.5
   | > preemphasis:0.98
   | > griffin_lim_iters:60
   | > signal_norm:True
   | > symmetric_norm:False
   | > mel_fmin:0.0
   | > mel_fmax:8000.0
   | > max_norm:1.0
   | > clip_norm:True
   | > do_trim_silence:True
   | > n_fft:2048
   | > hop_length:200
   | > win_length:800
 > Setting up Audio Processor...
 | > fft size: 2048, hop length: 275, win length: 1102
 | > Audio Processor attributes.
   | > bits:None
   | > sample_rate:22050
   | > num_mels:80
   | > min_level_db:-100
   | > frame_shift_ms:12.5
   | > frame_length_ms:50
   | > ref_level_db:20
   | > num_freq:1025
   | > power:1.5
   | > preemphasis:0.98
   | > griffin_lim_iters:60
   | > signal_norm:True
   |

Tacotron(
  (embedding): Embedding(61, 256, padding_idx=5)
  (encoder): Encoder(
    (prenet): Prenet(
      (layers): ModuleList(
        (0): Linear(in_features=256, out_features=256, bias=True)
        (1): Linear(in_features=256, out_features=128, bias=True)
      )
      (relu): ReLU()
      (dropout): Dropout(p=0.5, inplace=False)
    )
    (cbhg): EncoderCBHG(
      (cbhg): CBHG(
        (relu): ReLU()
        (conv1d_banks): ModuleList(
          (0): BatchNormConv1d(
            (padder): ConstantPad1d(padding=[0, 0], value=0)
            (conv1d): Conv1d(128, 128, kernel_size=(1,), stride=(1,), bias=False)
            (bn): BatchNorm1d(128, eps=0.001, momentum=0.99, affine=True, track_running_stats=True)
            (activation): ReLU()
          )
          (1): BatchNormConv1d(
            (padder): ConstantPad1d(padding=[0, 1], value=0)
            (conv1d): Conv1d(128, 128, kernel_size=(2,), stride=(1,), bias=False)
            (bn): BatchNorm1d(128, eps=0.001, momentum=0

**Restore WaveRnn model**

In [ ]:
#from utils.generic_utils import load_config
from WaveRNN.models.wavernn import Model

bits = 10

wavernn = Model(
        rnn_dims=512,
        fc_dims=512,
        mode=VOCODER_CONFIG.mode,
        mulaw=VOCODER_CONFIG.mulaw,
        pad=VOCODER_CONFIG.pad,
        use_aux_net=VOCODER_CONFIG.use_aux_net,
        use_upsample_net=VOCODER_CONFIG.use_upsample_net,
        upsample_factors=VOCODER_CONFIG.upsample_factors,
        feat_dims=80,
        compute_dims=128,
        res_out_dims=128,
        res_blocks=10,
        hop_length=ap2.hop_length,
        sample_rate=ap2.sample_rate,
    ).cuda()



        
check = torch.load(VOCODER_MODEL_PATH)
wavernn.load_state_dict(check['model'])
if use_cuda:
    wavernn.cuda()
wavernn.eval();
print(check['step'])
    

560867


**Synthesize test sentences**

In [ ]:
# Define Test Sentences

test_sentences =[ "  A inauguração da vila é quarta ou quinta-feira",
        "  Vote se você tiver o título de eleitor",
        "  Hoje é fundamental encontrar a razão da existência humana",
        "  A temperatura é mais amena à noite",
        "  Em muitas cidades a população está diminuindo.",
        "  Nunca se deve ficar em cima do morro",
        "  Para as pessoas estranhas o panorama é desolador",
        "  É bom te ver colhendo flores menino",
        "  Eu finjo me banhar num lago ao amanhecer",
        "  Sua sensibilidade mostrará o caminho",
        "  A Amazônia é a reserva ecológica do globo",
        "  O ministério mudou demais com a eleição",
        "  Novas metas surgem na informática",
        "  O capital de uma empresa depende de sua produção",
        "  Se não fosse ela tudo teria sido melhor",
        "  A principal personagem no filme é uma gueixa",
        "  Espere seu amigo em casa",
        "  A juventude tinha que revolucionar a escola",
        "  A cantora terá quatro meses para ensaiar seu canto",
        "  Esse tema foi falado no congresso."]

model.decoder.max_decoder_steps = 250

In [ ]:
for idx, sentence in enumerate(test_sentences):
  align, spec, stop_tokens,wav,wav2 = tts(model, sentence, CONFIG, use_cuda, ap, figures=True,name=str(idx+1))
  print("arquivo gerado:",str(idx+1)+'.wav')
  ap.save_wav(wav, os.path.join(OUT_FOLDER,str(idx+1)+'.wav'))
  ap2.save_wav(wav2, os.path.join(OUT_FOLDER,str(idx+1)+'wavernn'+'.wav'))

 A inauguração da vila é quarta ou quinta-feira  -->  a inaʊɡuɾasɐ̃ʊ̃ da vilæ ɛ kwaɾətæ ow kiŋtæfeɪɾæ 
   | >Decoder stopped with Stop Token Loss


/usr/local/lib/python3.6/dist-packages/librosa/util/utils.py:1725: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  if np.issubdtype(x.dtype, float) or np.issubdtype(x.dtype, complex):


 >  Run-time with Griffin lim: 3.6123545169830322
 A inauguração da vila é quarta ou quinta-feira  -->  a inaʊɡuɾasɐ̃ʊ̃ da vilæ ɛ kwaɾətæ ow kiŋtæfeɪɾæ 
   | >Decoder stopped with Stop Token Loss
60000/60500 -- batch_size: 5 -- gen_rate: 4.5 kHz -- x_realtime: 0.3  
 >  Run-time with WaveRNN: 14.09778380393982


/usr/local/lib/python3.6/dist-packages/librosa/display.py:656: FutureWarning: Conversion of the second argument of issubdtype from `complex` to `np.complexfloating` is deprecated. In future, it will be treated as `np.complex128 == np.dtype(complex).type`.
  if np.issubdtype(data.dtype, np.complex):


Vocoder WaveRNN:


...

arquivo gerado: 18.wav
 A cantora terá quatro meses para ensaiar seu canto  -->  a kɐ̃ŋtoɾæ teɾa kwatrʊ mezys paɾæ eɪŋsaɪar seʊ kɐ̃ŋtʊ 
   | >Decoder stopped with Stop Token Loss
 >  Run-time with Griffin lim: 3.5392961502075195
 A cantora terá quatro meses para ensaiar seu canto  -->  a kɐ̃ŋtoɾæ teɾa kwatrʊ mezys paɾæ eɪŋsaɪar seʊ kɐ̃ŋtʊ 
   | >Decoder stopped with Stop Token Loss
72000/72600 -- batch_size: 6 -- gen_rate: 5.5 kHz -- x_realtime: 0.3  
 >  Run-time with WaveRNN: 14.001707792282104
Vocoder WaveRNN:


Vocoder Griffin-Lim :


arquivo gerado: 19.wav
 Esse tema foi falado no congresso.  -->  esi temæ foɪ faladʊ nʊ koŋɡrɛsʊ 
   | >Decoder stopped with Stop Token Loss
 >  Run-time with Griffin lim: 4.157937526702881
 Esse tema foi falado no congresso.  -->  esi temæ foɪ faladʊ nʊ koŋɡrɛsʊ 
   | >Decoder stopped with Stop Token Loss
84000/84700 -- batch_size: 7 -- gen_rate: 6.3 kHz -- x_realtime: 0.4  
 >  Run-time with WaveRNN: 14.235260248184204
Vocoder WaveRNN:


Vocoder Griffin-Lim :


arquivo gerado: 20.wav


**Synthesize sentence**


In [ ]:
import IPython
while True:
  frase = input("Enter sentence: ")
  if frase == 'q':
    break
  print('Input Text: ',frase)
  frase = '   '+frase
  align, spec, stop_tokens,wav,wav2 = tts(model, frase, CONFIG, use_cuda, ap, figures=True,name='teste')
  #IPython.display.display(Audio(wav, rate=ap.sample_rate))

Enter sentence: Curso 5 4º EABDA
Input Text:  Curso 5 4º EABDA
 Curso 5 4º EABDA  -->  kuɾəsʊ siŋku kwaɾətw eabdæ 
   | > Decoder stopped with 'max_decoder_steps


/usr/local/lib/python3.6/dist-packages/librosa/util/utils.py:1725: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  if np.issubdtype(x.dtype, float) or np.issubdtype(x.dtype, complex):


 >  Run-time with Griffin lim: 5.859762907028198
 Curso 5 4º EABDA  -->  kuɾəsʊ siŋku kwaɾətw eabdæ 
   | > Decoder stopped with 'max_decoder_steps
108000/108900 -- batch_size: 9 -- gen_rate: 7.8 kHz -- x_realtime: 0.5  
 >  Run-time with WaveRNN: 14.92134404182434


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:5: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  """
/content/TTS/utils/visual.py:54: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  plt.figure(figsize=(16, 32))
/usr/local/lib/python3.6/dist-packages/librosa/display.py:656: FutureWarning: Conversion of the second argument of issubdtype from `complex` to `np.complexfloating` is deprecated. In future, it will be treated as `np.complex128 == np.dtype(complex).type`.
  if np.issubdtype(data.dtype, np.complex):


Vocoder WaveRNN:


...

Enter sentence:  Curso 5, da 4ºa Escola Avançada de Big Data Analysis
Input Text:   Curso 5, da 4ºa Escola Avançada de Big Data Analysis
 Curso 5, da 4ºa Escola Avançada de Big Data Analysis  -->  kuɾəsʊ siŋku da kwatru oa eskɔlæ avɐ̃ŋsadæ dʒy biɡ datæ ænalizis 
   | > Decoder stopped with 'max_decoder_steps
 >  Run-time with Griffin lim: 5.718265056610107
 Curso 5, da 4ºa Escola Avançada de Big Data Analysis  -->  kuɾəsʊ siŋku da kwatru oa eskɔlæ avɐ̃ŋsadæ dʒy biɡ datæ ænalizis 
   | > Decoder stopped with 'max_decoder_steps
108000/108900 -- batch_size: 9 -- gen_rate: 8.2 kHz -- x_realtime: 0.5  
 >  Run-time with WaveRNN: 14.155412435531616
Vocoder WaveRNN:


Vocoder Griffin-Lim :


Enter sentence: Curso 5 da quarta Escola Avançada de Big Data Analysis
Input Text:  Curso 5 da quarta Escola Avançada de Big Data Analysis
 Curso 5 da quarta Escola Avançada de Big Data Analysis  -->  kuɾəsʊ siŋku da kwaɾətæ eskɔlæ avɐ̃ŋsadæ dʒy biɡ datæ ænalizis 
   | >Decoder stopped with Stop Token Loss
 >  Run-time with Griffin lim: 5.087270736694336
 Curso 5 da quarta Escola Avançada de Big Data Analysis  -->  kuɾəsʊ siŋku da kwaɾətæ eskɔlæ avɐ̃ŋsadæ dʒy biɡ datæ ænalizis 
   | >Decoder stopped with Stop Token Loss
96000/96800 -- batch_size: 8 -- gen_rate: 7.2 kHz -- x_realtime: 0.4  
 >  Run-time with WaveRNN: 14.338181018829346
Vocoder WaveRNN:


Vocoder Griffin-Lim :


Enter sentence: q
